# Test env

In [1]:

#imports
import os
import streamlit as st
from PIL import Image
from loguru import logger
# local imports
from ingest.ingester import Ingester
from query.querier import Querier
from summarize.summarizer import Summarizer
import settings
import utils as ut
from query.querier import EnumMode
from ingest.ingester import IngestionMode

import kamervragenEvaluation



In [2]:
SYSTEM_PROMPT= """
### OBJECTIVE ###
Je bent een assistent voor de rijksoverheid. Jouw taak is om vragen te beantwoorden in het Nederlands. Zorg ervoor dat je alleen antwoord geeft op basis van de beschikbare context en dat je daar ook naar verwijst in je antwoord.

### AUDIENCE ###
De doelgroep van jouw antwoorden zijn ambtenaren. Geef alle relevante informatie uit de context, antwoord in het Nederlands leg in maximaal 100 woorden zoveel mogelijk uit.

### GUARDRAILS ###
Indien de context onvoldoende informatie bevat om de vraag te beantwoorden, verzin dan geen informatie maar geef aan dat er onvoldoende informatie beschikbaar is.

### INSTRUCTIONS ###
- Beantwoord de vraag altijd in het Nederlands, zelfs als de context in het Engels is gesteld.
- Vermijd het herhalen van de vraag in het antwoord en het herhalen van de instructies. Voer de instructies uit en geef een concreet antwoord op de gestelde vraag.
- Geef een stapsgewijze redenering bij het beantwoorden van de vraag en refereer naar specifieke zinnen uit de context die hebben bijgedragen aan het antwoord.
- Houd je antwoord nauw verbonden met de context en vermijd het toevoegen van informatie die niet expliciet in de context wordt vermeld.

- Voor meer informatie over de context, zeg het bestandsnaam die gevonden is in de source_document. Mits deze beschikbaar is.
### QUESTION ### \n
"""

In [3]:
# Commented the settings that arent used as parameters in the functions

# DOC_DIR = "./docs"
# CHUNK_DIR = "./chunks"
# VECDB_DIR = "./vector_stores"
# EVAL_DIR = "./evaluate"
# EVAL_APP_HEADER = "Evaluation"
# EVAL_APP_INFO = "./info/evaluation_explanation.txt"
# EVAL_FILE_NAME = "eval.json"
# CHAIN_VERBOSITY = False
LLM_TYPE = "local_llm"
LLM_MODEL_TYPE = "gemma2"
# API_URL = "http://127.0.0.1:11434"
AZUREOPENAI_API_VERSION = "2023-08-01-preview"
EMBEDDINGS_PROVIDER = "local_embeddings"
EMBEDDINGS_MODEL = "textgain/allnli-GroNLP-bert-base-dutch-cased"
TEXT_SPLITTER_METHOD = "NLTKTextSplitter"
# CHAIN_NAME = "conversationalretrievalchain"
# CHAIN_TYPE = "stuff"
# SEARCH_TYPE = "similarity"
# SCORE_THRESHOLD = 0.5
VECDB_TYPE = "chromadb"
CHUNK_SIZE = 1024
# CHUNK_K = 4
CHUNK_OVERLAP = 256
# RETRIEVAL_METHOD = "regular"


folderSelected = "kamerVragen"
my_folder_path_selected, my_vectordb_folder_path_selected = ut.create_vectordb_name(folderSelected)

CONCAT_FILES = True


In [4]:
SPLITTING_METHODS = [IngestionMode.question_answer,IngestionMode.token_small,IngestionMode.token_medium,IngestionMode.token_large]
CONTEXT_PRESENT= [True, False]
EMBEDDINGS_MODELS = ["GroNLP/bert-base-dutch-cased","textgain/allnli-GroNLP-bert-base-dutch-cased", "sentence-transformers/paraphrase-multilingual-MiniLM-L12-v2"]

In [5]:
querier = None
ingester = None

def init(LLM_TYPE=LLM_TYPE, LLM_MODEL_TYPE=LLM_MODEL_TYPE, EMBEDDINGS_MODEL=EMBEDDINGS_MODEL, EMBEDDINGS_PROVIDER=EMBEDDINGS_PROVIDER, AZUREOPENAI_API_VERSION=AZUREOPENAI_API_VERSION, TEXT_SPLITTER_METHOD=TEXT_SPLITTER_METHOD, CHUNK_SIZE=CHUNK_SIZE, CHUNK_OVERLAP=CHUNK_OVERLAP, VECDB_TYPE=VECDB_TYPE, vectordb_folder= my_vectordb_folder_path_selected, content_folder=my_folder_path_selected):
  # Init
  querier = Querier(
    llm_type=LLM_TYPE, 
    llm_model_type=LLM_MODEL_TYPE, 
    embeddings_model=EMBEDDINGS_MODEL, 
    embeddings_provider=EMBEDDINGS_PROVIDER, 
    azureopenai_api_version=AZUREOPENAI_API_VERSION
    )

  ingester = Ingester(
    collection_name=folderSelected, 
    content_folder=content_folder, 
    vectordb_folder=vectordb_folder,
    embeddings_model=EMBEDDINGS_MODEL,
    text_splitter_method=TEXT_SPLITTER_METHOD,
    chunk_size=CHUNK_SIZE,
    chunk_overlap=CHUNK_OVERLAP,
    vecdb_type=VECDB_TYPE
    )
  return [querier,ingester]
  
# querier,ingester = init()


In [6]:
def ingest(mode=IngestionMode.question_answer_per_page, forceRebuild=True, addedMetaDataURLCSV="docs/metadata.csv", addContext=True):
  ingester.ingest(mode=mode, forceRebuild=forceRebuild, addedMetaDataURLCSV=addedMetaDataURLCSV, addContext=addContext)
# ingest()

In [7]:
def chain(vectorDBPATH = my_vectordb_folder_path_selected):
  querier.make_chain(folderSelected, vectorDBPATH)
# chain()

In [8]:
# querier.ask_question("""
#                      Kwamen er 82 treinen stil te staan tijdens hun rit?
#                      """, mode=EnumMode.metadata, system_prompt_override=SYSTEM_PROMPT)

## Place folder contents in json file

In [9]:


# from chunker import clean_pages
# from ingest.file_parser import FileParser
# import json 

# processed = []
# file_parser = FileParser()

# # Process files
# for file in os.listdir(my_folder_path_selected):
#   if not file.endswith(".pdf"):
#     continue
#   print("start processing file: ", file)
#   file_path = os.path.join(my_folder_path_selected, file)
#   raw_pages, _ = file_parser.parse_file(file_path)
#   cleaned_pages = clean_pages(raw_pages)
#   processed.extend(cleaned_pages)

# # Write processed pages to json file
# print("writing processed pages to json file")
# output_file = os.path.join(my_folder_path_selected, "processed.json")

# with open(output_file, "w") as f:
#   json.dump(processed, f)

# print("done")
  



In [10]:
for time in range(10):
  for splittingMethod in SPLITTING_METHODS:
    for context in CONTEXT_PRESENT:
      for embeddingModel in EMBEDDINGS_MODELS:
        chunk_size = CHUNK_SIZE
        if splittingMethod == IngestionMode.token_small:
          chunk_size = 128
        elif splittingMethod == IngestionMode.token_medium:
          chunk_size = 512
        elif splittingMethod == IngestionMode.token_large:
          chunk_size = 1024
          
        # Setup
        my_folder_path_selected, my_vectordb_folder_path_selected = ut.create_vectordb_name(folderSelected, chunk_size=chunk_size, chunk_overlap=0, splitting_method=splittingMethod, embeddings_model=embeddingModel, added_context=context)
        querier,ingester = init(EMBEDDINGS_MODEL=embeddingModel, vectordb_folder=my_vectordb_folder_path_selected)
        # Ingestion
        ingest(mode=splittingMethod, addContext=context, addedMetaDataURLCSV="docs/metadata.csv")
        # RAG CHAIN
        chain(vectorDBPATH=my_vectordb_folder_path_selected)
        
        # Evaluation
        kamervragenEvaluation.test_retrival(
            my_folder_path_selected, 
            ingester, 
            querier=querier, 
            toCSV=True,
            ingestionMode=splittingMethod, 
            addedMetaDataURLCSV="docs/metadata.csv", 
            addContext=context,
            embeddings_model=embeddingModel,
            text_splitter_method=TEXT_SPLITTER_METHOD,
            embeddings_provider=EMBEDDINGS_PROVIDER,
            database=VECDB_TYPE,
            ConcatFiles=CONCAT_FILES,
        )
        
        
        
        print("done")
  print(f"Done with iteration {time}")

/Users/markheijnekamp/Documents/GitHub/LearningLion-kamervragen/utils.py:113: LangChainDeprecationWarning: The class `HuggingFaceEmbeddings` was deprecated in LangChain 0.2.2 and will be removed in 1.0. An updated version of the class exists in the :class:`~langchain-huggingface package and should be used instead. To use it run `pip install -U :class:`~langchain-huggingface` and import as `from :class:`~langchain_huggingface import HuggingFaceEmbeddings``.
  embeddings = HuggingFaceEmbeddings(
/opt/homebrew/lib/python3.11/site-packages/sentence_transformers/cross_encoder/CrossEncoder.py:13: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from tqdm.autonotebook import tqdm, trange
No sentence-transformers model found with name GroNLP/bert-base-dutch-cased. Creating a new one with mean pooling.
Some weights of BertModel were not initialized from the model checkpoint at GroNLP/bert-base-dutch-cased

writing to csv
done writing to csv
done


/opt/homebrew/lib/python3.11/site-packages/transformers/tokenization_utils_base.py:1617: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be deprecated in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(
2024-10-01 16:56:41.509 | INFO     | utils:getEmbeddings:118 - Loaded local embeddings: textgain/allnli-GroNLP-bert-base-dutch-cased
2024-10-01 16:56:41.509 | INFO     | llm_class.llm_class:__init__:38 - Use Local LLM
2024-10-01 16:56:41.509 | INFO     | llm_class.llm_class:__init__:39 - Retrieving gemma2
2024-10-01 16:56:41.509 | INFO     | llm_class.llm_class:__init__:41 - Using local api url http://127.0.0.1:11434
2024-10-01 16:56:41.510 | INFO     | llm_class.llm_class:__init__:52 - Retrieved gemma2
/opt/homebrew/lib/python3.11/site-packages/transformers/tokenization_utils_base.py:1617: FutureWa

writing to csv
done writing to csv
done


/opt/homebrew/lib/python3.11/site-packages/transformers/tokenization_utils_base.py:1617: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be deprecated in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(
2024-10-01 16:56:49.537 | INFO     | utils:getEmbeddings:118 - Loaded local embeddings: sentence-transformers/paraphrase-multilingual-MiniLM-L12-v2
2024-10-01 16:56:49.537 | INFO     | llm_class.llm_class:__init__:38 - Use Local LLM
2024-10-01 16:56:49.537 | INFO     | llm_class.llm_class:__init__:39 - Retrieving gemma2
2024-10-01 16:56:49.537 | INFO     | llm_class.llm_class:__init__:41 - Using local api url http://127.0.0.1:11434
2024-10-01 16:56:49.538 | INFO     | llm_class.llm_class:__init__:52 - Retrieved gemma2
/opt/homebrew/lib/python3.11/site-packages/transformers/tokenization_utils_base.py

...

writing to csv
done writing to csv
done


/opt/homebrew/lib/python3.11/site-packages/transformers/tokenization_utils_base.py:1617: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be deprecated in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(
2024-10-01 17:02:32.860 | INFO     | utils:getEmbeddings:118 - Loaded local embeddings: textgain/allnli-GroNLP-bert-base-dutch-cased
2024-10-01 17:02:32.861 | INFO     | llm_class.llm_class:__init__:38 - Use Local LLM
2024-10-01 17:02:32.861 | INFO     | llm_class.llm_class:__init__:39 - Retrieving gemma2
2024-10-01 17:02:32.861 | INFO     | llm_class.llm_class:__init__:41 - Using local api url http://127.0.0.1:11434
2024-10-01 17:02:32.862 | INFO     | llm_class.llm_class:__init__:52 - Retrieved gemma2
/opt/homebrew/lib/python3.11/site-packages/transformers/tokenization_utils_base.py:1617: FutureWa

writing to csv
done writing to csv
done


/opt/homebrew/lib/python3.11/site-packages/transformers/tokenization_utils_base.py:1617: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be deprecated in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(
2024-10-01 17:02:44.566 | INFO     | utils:getEmbeddings:118 - Loaded local embeddings: sentence-transformers/paraphrase-multilingual-MiniLM-L12-v2
2024-10-01 17:02:44.566 | INFO     | llm_class.llm_class:__init__:38 - Use Local LLM
2024-10-01 17:02:44.566 | INFO     | llm_class.llm_class:__init__:39 - Retrieving gemma2
2024-10-01 17:02:44.567 | INFO     | llm_class.llm_class:__init__:41 - Using local api url http://127.0.0.1:11434
2024-10-01 17:02:44.567 | INFO     | llm_class.llm_class:__init__:52 - Retrieved gemma2
/opt/homebrew/lib/python3.11/site-packages/transformers/tokenization_utils_base.py

writing to csv
done writing to csv
done


## Evaluations

In [11]:
import kamervragenEvaluation


### Check if one single file can be retrived

In [12]:

kamervragenEvaluation.test_retrival(
  my_folder_path_selected, 
  ingester, 
  querier=querier, 
  toCSV=True,
  ingestionMode=IngestionMode.question_answer_per_page, 
  addedMetaDataURLCSV="docs/metadata.csv", 
  addContext=True,
  embeddings_model=EMBEDDINGS_MODEL,
  text_splitter_method=TEXT_SPLITTER_METHOD,
  embeddings_provider=EMBEDDINGS_PROVIDER,
  database=VECDB_TYPE,
  ConcatFiles=CONCAT_FILES
  )

2024-10-01 17:02:52.997 | INFO     | ingest.file_parser:parse_pdf:50 - Extracting metadata
2024-10-01 17:02:52.997 | INFO     | ingest.file_parser:parse_pdf:53 - None
2024-10-01 17:02:52.998 | INFO     | ingest.file_parser:parse_pdf:55 - Extracting pages
2024-10-01 17:02:53.106 | INFO     | query.querier:get_documents_with_scores:133 - Topscore most similar docs: 0.6872509121894836
2024-10-01 17:02:53.119 | INFO     | query.querier:get_documents_with_scores:133 - Topscore most similar docs: 0.6872509121894836
2024-10-01 17:02:53.120 | INFO     | kamervragenEvaluation:test_retrival_singular:25 - Highest score: 0.6872509121894836
2024-10-01 17:02:53.120 | INFO     | kamervragenEvaluation:test_retrival_singular:30 - Source document not found
2024-10-01 17:02:53.133 | INFO     | query.querier:get_documents_with_scores:133 - Topscore most similar docs: 0.39540159702301025
2024-10-01 17:02:53.146 | INFO     | query.querier:get_documents_with_scores:133 - Topscore most similar docs: 0.3954015

writing to csv
done writing to csv


In [13]:
kamervragenEvaluation.store_questions_and_answers_CSV(my_folder_path_selected, ingester,concatFiles=CONCAT_FILES)

2024-10-01 17:02:56.347 | INFO     | ingest.file_parser:parse_pdf:50 - Extracting metadata
2024-10-01 17:02:56.348 | INFO     | ingest.file_parser:parse_pdf:53 - None
2024-10-01 17:02:56.348 | INFO     | ingest.file_parser:parse_pdf:55 - Extracting pages
2024-10-01 17:02:56.419 | INFO     | ingest.file_parser:parse_pdf:50 - Extracting metadata
2024-10-01 17:02:56.420 | INFO     | ingest.file_parser:parse_pdf:53 - None
2024-10-01 17:02:56.420 | INFO     | ingest.file_parser:parse_pdf:55 - Extracting pages
2024-10-01 17:02:56.442 | INFO     | ingest.file_parser:parse_pdf:50 - Extracting metadata
2024-10-01 17:02:56.443 | INFO     | ingest.file_parser:parse_pdf:53 - None
2024-10-01 17:02:56.443 | INFO     | ingest.file_parser:parse_pdf:55 - Extracting pages
2024-10-01 17:02:56.488 | INFO     | ingest.file_parser:parse_pdf:50 - Extracting metadata
2024-10-01 17:02:56.489 | INFO     | ingest.file_parser:parse_pdf:53 - None
2024-10-01 17:02:56.489 | INFO     | ingest.file_parser:parse_pdf:55

done writing to csv


In [14]:
kamervragenEvaluation.test_retrival_map_grading(
  my_folder_path_selected, 
  ingester, 
  querier=querier, 
  toCSV=True,
  ingestionMode=IngestionMode.question_answer_per_page, 
  addedMetaDataURLCSV="docs/metadata.csv", 
  addContext=True,
  embeddings_model=EMBEDDINGS_MODEL,
  text_splitter_method=TEXT_SPLITTER_METHOD,
  embeddings_provider=EMBEDDINGS_PROVIDER,
  database=VECDB_TYPE,
  concatFiles=CONCAT_FILES)

2024-10-01 17:02:57.590 | INFO     | ingest.file_parser:parse_pdf:50 - Extracting metadata
2024-10-01 17:02:57.590 | INFO     | ingest.file_parser:parse_pdf:53 - None
2024-10-01 17:02:57.591 | INFO     | ingest.file_parser:parse_pdf:55 - Extracting pages
2024-10-01 17:02:57.735 | INFO     | query.querier:get_documents_with_scores:133 - Topscore most similar docs: 0.6872509121894836
2024-10-01 17:02:57.742 | INFO     | ingest.file_parser:parse_pdf:50 - Extracting metadata
2024-10-01 17:02:57.743 | INFO     | ingest.file_parser:parse_pdf:53 - None
2024-10-01 17:02:57.743 | INFO     | ingest.file_parser:parse_pdf:55 - Extracting pages
2024-10-01 17:02:57.787 | INFO     | query.querier:get_documents_with_scores:133 - Topscore most similar docs: 0.7927170991897583
2024-10-01 17:02:57.793 | INFO     | ingest.file_parser:parse_pdf:50 - Extracting metadata
2024-10-01 17:02:57.794 | INFO     | ingest.file_parser:parse_pdf:53 - None
2024-10-01 17:02:57.794 | INFO     | ingest.file_parser:parse_p

done writing to csv
